# Add working conditions data from EWCS

### Load libraries

In [1]:
import pandas as pd
import pyreadstat

### Load data

In [2]:
df, meta = pyreadstat.read_dta(
    "/Users/alexandralugova/Documents/GitHub/MH-old-workers/data/datasets/EWCS 1991-2015 UKDA ISCO.DTA"
)
variable_labels = meta.column_labels

In [3]:
df

id  countid  wave  year y15_Q1 y15_Q2a y15_Q2b y15_Q2c  \
0           BE000964        1     6  2015      1       1      40       1   
1           BE000967        1     6  2015      1       2      49       1   
2           BE000968        1     6  2015      2       1      54       1   
3           BE000970        1     6  2015      3       1      52       1   
4           BE000972        1     6  2015      3       1      28       1   
...              ...      ...   ...   ...    ...     ...     ...     ...   
178900         21034       27     1  1991      5       1      36     NaN   
178901         21037       27     1  1991      3       2      32     NaN   
178902         21042       27     1  1991      4       1      17     NaN   
178903         21045       27     1  1991      4       1      23     NaN   
178904         21051       27     1  1991      2       1      32     NaN   

       y15_Q2d y15_Q3a_2  ...    wq_slim    goodsoc     envsec     intens  \
0            2       NaN  ...  14.285715  94.444443  66.666664  31.759258   
1            2       NaN  ...  85.714287        NaN  91.025642  13.148149   
2            2         2  ...  85.714287        NaN  76.923080  27.037039   
3            2         2  ...  28.571430  97.916664  98.717949   9.444445   
4            2         1  ...  42.857143  74.166664  97.435898  30.833334   
...        ...       ...  ...        ...        ...        ...        ...   
178900     NaN       NaN  ...        NaN        NaN        NaN        NaN   
178901     NaN       NaN  ...        NaN        NaN        NaN        NaN   
178902     NaN       NaN  ...        NaN        NaN        NaN        NaN   
178903     NaN       NaN  ...        NaN        NaN        NaN        NaN   
178904     NaN       NaN  ...        NaN        NaN        NaN        NaN   

       intens_slim      prosp       wlb wlb_slim ISCO_08 ISCO_88  
0        53.333336  25.000000  69.12500   88.500    8141    8231  
1        24.444445  50.000000  84.50000   87.500    5141    5141  
2        52.222221  50.000000  56.31250   37.500    1323    1313  
3        18.888889  62.500000  86.84375   96.875    7115    7124  
4        53.333336  41.666664  74.28125   96.875    8322    8322  
...            ...        ...       ...      ...     ...     ...  
178900         NaN        NaN       NaN      NaN     NaN     NaN  
178901         NaN        NaN       NaN      NaN     NaN     NaN  
178902         NaN        NaN       NaN      NaN     NaN     NaN  
178903         NaN        NaN       NaN      NaN     NaN     NaN  
178904         NaN        NaN       NaN      NaN     NaN     NaN  

[178905 rows x 751 columns]

### Choose only necessary data, tranform where needed

Identify and name the aggregated indexes for work conditions

In [4]:
labels_to_search = [
    "JQI Monthly earnings",
    "JQI Skills and discretion index",
    "JQI social environment",
    "JQI Physical environment index",
    "JQI Intensity index",
    "JQI SLIM Intensity index",
    "JQI Prospects index",
    "JQI Working time quality index",
    "JQI SLIM Working time quality index",
]

# Iterate through metadata to find labels and print corresponding variable names
for index, label in enumerate(meta.column_labels):
    if label in labels_to_search:
        print(label, ":", meta.column_names[index])

JQI Monthly earnings : adincome_mth
JQI Skills and discretion index : wq
JQI social environment : goodsoc
JQI Physical environment index : envsec
JQI Intensity index : intens
JQI SLIM Intensity index : intens_slim
JQI Prospects index : prosp
JQI Working time quality index : wlb
JQI SLIM Working time quality index : wlb_slim


In [5]:
df = df.rename(
    columns={
        "adincome_mth": "jqi_monthly_earnings",
        "wq": "jqi_skills_discretion",
        "goodsoc": "jqi_social_environment",
        "envsec": "jqi_physical_environment",
        "intens_slim": "jqi_intensity",
        "prosp": "jqi_prospects",
        "wlb": "jqi_working_time_quality",
    }
)

Choose columns

In [6]:
df = df[
    [
        "id",
        "countid",
        "year",
        "ISCO_08",
        "jqi_monthly_earnings",
        "jqi_skills_discretion",
        "jqi_social_environment",
        "jqi_physical_environment",
        "jqi_intensity",
        "jqi_prospects",
        "jqi_working_time_quality",
    ]
]

Define country names and choose the needed

In [7]:
countid_mapping = meta.value_labels["COUNTID"]
df["countid"] = df["countid"].map(countid_mapping)

In [8]:
countries = [
    "Austria",
    "Belgium",
    "Czech Republic",
    "Denmark",
    "Estonia",
    "France",
    "Germany",
    "Italy",
    "Slovenia",
    "Spain",
    "Switzerland",
]
df = df[df["countid"].isin(countries)].reset_index(drop=True)

Leave only waves 5 and 6 (2010 and 2015)

In [9]:
df = df[df.year >= 2010].reset_index(drop=True)

Drop lines with missing isco codes

In [10]:
df = df.dropna(subset="ISCO_08").reset_index(drop=True)

Adjust some isco codes

In [11]:
def modify_isco(value):
    if len(str(value)) == 1:
        return value * 1000
    elif len(str(value)) == 2:
        return value * 100
    elif len(str(value)) == 3:
        return value * 10
    else:
        return value


df["ISCO_08"] = df["ISCO_08"].apply(modify_isco)

Rename some variables

In [12]:
df = df.rename(columns={"countid": "country", "ISCO_08": "isco"})

In [32]:
df

id   country  year  isco  jqi_monthly_earnings  \
0          BE000964   Belgium  2015  8141           1530.153076   
1          BE000967   Belgium  2015  5141                   NaN   
2          BE000968   Belgium  2015  1323           1800.180054   
3          BE000970   Belgium  2015  7115           1575.157593   
4          BE000972   Belgium  2015  8322           1278.127930   
...             ...       ...   ...   ...                   ...   
34701   23000011509  Slovenia  2010  9111             99.932480   
34702   23000011511  Slovenia  2010  5131            624.578003   
34703   23000011513  Slovenia  2010  5141            437.204590   
34704   23000011516  Slovenia  2010  3113            749.493591   
34705   23000011713  Slovenia  2010  2434           1498.987183   

       jqi_skills_discretion  jqi_social_environment  \
0                   8.536879               94.444443   
1                  64.617447                     NaN   
2                  76.372818                     NaN   
3                  42.832993               97.916664   
4                  30.789835               74.166664   
...                      ...                     ...   
34701              41.638947                     NaN   
34702              48.814400                     NaN   
34703              60.634476                     NaN   
34704              89.690376                     NaN   
34705              75.626358                     NaN   

       jqi_physical_environment  jqi_intensity  jqi_prospects  \
0                     66.666664      53.333336      25.000000   
1                     91.025642      24.444445      50.000000   
2                     76.923080      52.222221      50.000000   
3                     98.717949      18.888889      62.500000   
4                     97.435898      53.333336      41.666664   
...                         ...            ...            ...   
34701                 84.615387      40.000000            NaN   
34702                 84.615387      40.000000            NaN   
34703                 80.769234       6.666667            NaN   
34704                 97.435898      18.888889            NaN   
34705                 74.358971      74.444443            NaN   

       jqi_working_time_quality  
0                      69.12500  
1                      84.50000  
2                      56.31250  
3                      86.84375  
4                      74.28125  
...                         ...  
34701                       NaN  
34702                       NaN  
34703                       NaN  
34704                       NaN  
34705                       NaN  

[34706 rows x 11 columns]

### Calculate social environment, job prospects and working time quality indexes for 2010

In [21]:
df10, meta10 = pyreadstat.read_dta(
    "/Users/alexandralugova/Documents/GitHub/MH-old-workers/data/datasets/UKDA-2010/stata/stata11/ewcs_2010_version_ukda_6_dec_2011.dta"
)

Modify the formatting of id column

In [22]:
df10["id"] = df10["id"].astype("str")
df10["id"] = df10["id"].str.strip()
df10["id"] = df10["id"].str.replace(r"[^ -~]+", "", regex=True)

Calculate the social environment index

In [23]:
intens = df10[
    [
        "id",
        "q45a",
        "q45b",
        "q46a",
        "q46b",
        "q46c",
        "q46d",
        "q46e",
        "q47",
        "q48",
        "q51g",
        "q51p",
        "q24g",
    ]
]

In [26]:
len(intens)

29588

In [25]:
# Eliminate data with refusals or "don't know" answers
intensity_columns = [
    "q45a",
    "q45b",
    "q46a",
    "q46b",
    "q46c",
    "q46d",
    "q46e",
    "q47",
    "q48",
    "q51g",
    "q51p",
    "q24g",
]
for col in intensity_columns:
    intens = intens[intens[col] < 8].reset_index(drop=True)

In [31]:
df.jqi_intensity.describe()

count    34615.000000
mean        41.386875
std         25.259506
min          0.000000
25%         20.000000
50%         40.000000
75%         59.999996
max        100.000000
Name: jqi_intensity, dtype: float64

In [27]:
# Calculate frequent disruptive interruptions
intens["q4748"] = intens["q47"] * intens["q48"]
# Calculate cases where there are three or more pace determinants
intens["q46"] = 2
for i in range(len(intens)):
    count = 0
    for col in ["q46a", "q46b", "q46c", "q46d", "q46e"]:
        if intens[col][i] == 1:
            count += 1
    if count >= 3:
        intens["q46"][i] = 1

/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_41220/1539666845.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  intens["q46"][i] = 1
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_41220/1539666845.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  intens["q46"][i] = 1
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_41220/1539666845.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  intens["q4

### Aggregate on the level of isco, year and country

In [14]:
df = df.groupby(["country", "year", "isco"]).mean().reset_index(drop=False)

In [15]:
df = df.dropna().reset_index(drop=True)

Interpolate to obtain approximation of values for 2011 and 2013

In [16]:
# Convert 'year' column to datetime
df["year"] = pd.to_datetime(df["year"], format="%Y")

# Create DataFrames for years 2010 and 2015 separately
df_2010 = df[df["year"].dt.year == 2010]
df_2015 = df[df["year"].dt.year == 2015]

# Create an empty DataFrame for years 2011 and 2013
df_2011 = pd.DataFrame()
df_2013 = pd.DataFrame()

# Loop through unique combinations of 'country' and 'isco'
for country in df["country"].unique():
    for isco in df["isco"].unique():
        # Filter data for specific 'country' and 'isco' combination
        data_2010 = df_2010[(df_2010["country"] == country) & (df_2010["isco"] == isco)]
        data_2015 = df_2015[(df_2015["country"] == country) & (df_2015["isco"] == isco)]

        # Interpolate values for 'year' 2011 and 'year' 2013 if data for both 2010 and 2015 exists
        if not data_2010.empty and not data_2015.empty:
            # Calculate the interpolation for each column for 'year' 2011
            interpolated_values_2011 = data_2010.iloc[0, 3:].interpolate(
                method="linear", limit_area="inside", limit=1
            ) + (data_2015.iloc[0, 3:] - data_2010.iloc[0, 3:]).multiply(1 / 3)

            # Calculate the interpolation for each column for 'year' 2013
            interpolated_values_2013 = data_2010.iloc[0, 3:].interpolate(
                method="linear", limit_area="inside", limit=1
            ) + (data_2015.iloc[0, 3:] - data_2010.iloc[0, 3:]).multiply(3 / 5)

            # Give names to the interpolated values based on column names
            interpolated_values_2011.index = data_2010.columns[3:]
            interpolated_values_2013.index = data_2010.columns[3:]

            # Create DataFrame rows for 'year' 2011 and 'year' 2013 with interpolated values
            row_2011 = pd.DataFrame(
                {
                    "country": [country],
                    "year": [pd.Timestamp(year=2011, month=1, day=1)],
                    "isco": [isco],
                }
            ).join(interpolated_values_2011.to_frame().T.reset_index(drop=True))

            row_2013 = pd.DataFrame(
                {
                    "country": [country],
                    "year": [pd.Timestamp(year=2013, month=1, day=1)],
                    "isco": [isco],
                }
            ).join(interpolated_values_2013.to_frame().T.reset_index(drop=True))

            # Append the interpolated values for 'year' 2011 and 'year' 2013 to their respective DataFrames
            df_2011 = pd.concat([df_2011, row_2011], ignore_index=True)
            df_2013 = pd.concat([df_2013, row_2013], ignore_index=True)

# Append the interpolated 'year' 2011 and 'year' 2013 data to the original DataFrame
df = pd.concat([df, df_2011, df_2013], ignore_index=True)
df["year"] = pd.to_datetime(df["year"], format="%Y")
df["year"] = df["year"].dt.year

/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_39622/2611807505.py:22: FutureWarning: Series.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  interpolated_values_2011 = data_2010.iloc[0, 3:].interpolate(method='linear', limit_area='inside', limit=1) + \
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_39622/2611807505.py:26: FutureWarning: Series.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  interpolated_values_2013 = data_2010.iloc[0, 3:].interpolate(method='linear', limit_area='inside', limit=1) + \
/var/folders/ck/3npmnx597nb730qdy5w_6kp00000gn/T/ipykernel_39622/2611807505.py:22: FutureWarning: Series.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  interpolated_values_

In [17]:
df

country  year  isco jqi_monthly_earnings jqi_skills_discretion  \
0     Austria  2010  1114          2366.148112             77.290234   
1     Austria  2010  1120          3143.596761             83.616787   
2     Austria  2010  1219          1588.023401              64.30635   
3     Austria  2010  1221          3194.299927             86.929178   
4     Austria  2010  1321          2788.674561             66.906092   
...       ...   ...   ...                  ...                   ...   
8169    Spain  2013  9334          1046.085136             39.659487   
8170    Spain  2013  2100          2069.535937             66.338245   
8171    Spain  2013  2143          2022.221924             68.003346   
8172    Spain  2013  3258          1435.902368             67.310957   
8173    Spain  2013  7533           617.640436               43.9013   

     jqi_physical_environment jqi_intensity_slim jqi_working_time_quality_slim  
0                   97.863248          45.925926                         100.0  
1                   85.042736           50.74074                        53.125  
2                   89.903848          25.694444                      85.15625  
3                   95.512821           57.77778                      85.15625  
4                   72.863248          48.611112                       60.0625  
...                       ...                ...                           ...  
8169                81.911422          53.606061                     82.545455  
8170                 88.46154          49.999997                         98.75  
8171                 87.94872          66.222223                        70.625  
8172                 71.28205          40.222222                          68.7  
8173                82.365386          47.916668                     83.921875  

[8174 rows x 8 columns]

In [18]:
df.to_csv(
    "/Users/alexandralugova/Documents/GitHub/MH-old-workers/data/datasets/work_quality_indexes.csv",
    index=False,
)